In [5]:
import pandas as pd
from geopy.geocoders import Nominatim
#Importación del módulo csv que necesitaremos para leer y escribir en nuestros csv
import csv
#Importación del módulo shutil que usaremos para crear una copia de nuestro csv original
import shutil
import geopandas as gpd
import matplotlib.pyplot as plt
import networkx as nx
import osmnx as ox
import pyrematch as re
from shapely.geometry import shape
import numpy as np
import networkx as nx
from time import time 
from pyproj import CRS
from collections import OrderedDict
import operator
from functools import reduce


# Insertar costos a los arcos de Santiago

**Creamos el grafo de Santiago**

In [6]:
place_name = "Provincia de Santiago, Región Metropolitana de Santiago, Chile"
graph = ox.graph_from_place(place_name, network_type = "drive", simplify = False)

In [7]:
ox.speed.add_edge_speeds(graph, hwy_speeds=None, fallback=None, precision=1)

**Obtenemos los df de nodos y arcos**

In [8]:
nodes, edges = ox.graph_to_gdfs(graph)

**Agregamos columna de tiempo de viaje**

In [9]:
edges['Tiempos de Viaje'] = 0
edges['Tiempos de Viaje'] = edges.apply(lambda x: ((edges['length']/1000)/edges['speed_kph'])) #horas

**Creamos función que disminuirá la velocidad  del los arcos, dependiendo de la hora y minuto del día**

**Funciones que servirán para dar efecto congestión**

In [10]:
def interpolacion_lineal(x,x1,x2,y1,y2):
    y = ((y2-y1)/(x2-x1))*(x-x1)+y1
    return(y)

In [11]:
def interpolacion_cuadratica(x, fx):
    b0 = fx[0]
    b1 = (fx[1]-fx[0])/(x[1]-x[0])
    b2 = (((fx[2]-fx[1])/(x[2]-x[1]))-((fx[1]-fx[0])/(x[1]-x[0])))/(x[2]-x[0])
    f2 = b0+b1*(x[3]-x[0])+b2*(x[3]-x[0])*(x[3]-x[1])
    return(f2)

**Función tiempo final aplicada a la red**

In [12]:
def actualizar_tiempo(x, y, mes, hora, minutos): #x es velocidad e y es distancia
    y = y/1000
    dic_dism = {1:[(20.19/43.15),((20.19+14.09)/43.15),(18.51/43.15)],2:[(21.03/43.15),((21.03+14.09)/43.15),(19.14/43.15)], 3:[(16.89/43.15),((16.89+14.09)/43.15),(17.39/43.15)], 4:[(16.93/43.15),((16.93+14.09)/43.15),(17.38/43.15)], 5:[(17.19/43.15),((17.19+14.09)/43.15),(17.17/43.15)], 6:[(17.34/43.15),((17.34+14.09)/43.15),(17.08/43.15)], 7:[(18.46/43.15),((18.46+14.09)/43.15),(17.21/43.15)], 8:[(16.76/43.15),((16.76+14.09)/43.15),(16.94/43.15)], 9:[(17.15/43.15),((17.15+14.09)/43.15),(17.24/43.15)], 10:[(16.78/43.15),((16.78+14.09)/43.15),(17.02/43.15)], 11:[(16.57/43.15),((16.57+14.09)/43.15),(17.03/43.15)], 12:[(18.11/43.15),((18.11+14.09)/43.15),(17.13/43.15)]}
    #Punta mañana [0], Valle [1], Punta Tarde [2]
    if ((7 <= hora <= 8) and (0 <= minutos <= 59)):
        x = interpolacion_cuadratica([5, 8, 10.5, (hora+(minutos/60))], [x, x*dic_dism[mes][0], interpolacion_lineal(10.5,8,13.5,x*dic_dism[mes][0],x*dic_dism[mes][1])])
    elif ((9 <= hora <= 17) and (0 <= minutos <= 59)):
        x = interpolacion_cuadratica([10.5, 13.5, 16.25,(hora +(minutos/60))],[interpolacion_lineal(10.5,8,13.5,x*dic_dism[mes][0],x*dic_dism[mes][1]),x*dic_dism[mes][1], interpolacion_lineal(16.25,13.5,19,x*dic_dism[mes][1],x*dic_dism[mes][2])])
    elif ((18 <= hora <= 19) and (0 <= minutos <= 59)):
        x = interpolacion_cuadratica([16.25, 19, 22, (hora+(minutos/60))],[interpolacion_lineal(16.25,13.5,19,x*dic_dism[mes][1],x*dic_dism[mes][2]),x*dic_dism[mes][2],x])
    return (y/x) #horas

**Ahora probamos la función para los diferentes horarios**

00:03 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

8:33 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

10:32 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

13:00 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

13:30 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

18:20 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

**Función Dijsktra dependiente del tiempo**

In [13]:
def subgrafo(graph, src, direccion_x, direccion_y, m, n):
    subgrafo = nx.ego_graph(graph, src, radius = (ox.distance.great_circle_vec(direccion_x[m], direccion_y[m], direccion_x[n], direccion_y[n], earth_radius = 6371009)/100)+210, center=True, undirected=False, distance=None)
    return subgrafo

In [14]:
from heapq import *
def dijkstra_tiempo(graph, src, dest, mes, hora, minutos, visited = set(), times={}, predecessors={}):
    
    """ calculates a shortest path tree routed in src
    """    
    if src == dest:
        #print('LLEGÓ AL DESTINO------------------')
        # We build the shortest path and display it
        path=[]
        pred=dest
        while pred != None:
            path.append(pred)
            pred=predecessors.get(pred,None)
        # reverses the array, to display the path nicely
        readable=path[0]

        return(path, times[dest])
        
    else : 
        # if it is the initial  run, initializes the cost
        if not visited: 
            times[src] = 0
            
        #print('SRC', src)
        #print('graph', graph)
        for neighbor in graph[src] :
            print('neighbor', neighbor)
            print('visited', visited)
            if neighbor not in visited:
                x = graph[src][neighbor][0]['speed_kph']
                y = graph[src][neighbor][0]['length']
                act_time = actualizar_tiempo(x, y, mes, hora, minutos) #horas
                new_time = times[src] + act_time # tiempo acumulado en horas
                if new_time < times.get(neighbor,float('inf')):
                    times[neighbor] = new_time
                    predecessors[neighbor] = src
                    print(predecessors)

        visited.add(src)
        unvisited=[]
        
        for k in graph:
            if k not in visited:
                heappush(unvisited, (times.get(k, float('inf')), k))   

        nodo_actual = heappop(unvisited)[1] 
        return dijkstra_tiempo(graph, nodo_actual, dest, mes, hora, minutos, visited, times, predecessors)  

In [15]:
def vecino_cercano(graph, src, dest, mes, hora, minutos, new_time = 0, visited={}, historico={}, betados=set(), predecessors={}):
    visited.add(src)
    """ calculates a shortest path tree routed in src
    """    
    if src == dest:
        #print('LLEGÓ AL DESTINO------------------')
        # We build the shortest path and display it
        path=[]
        pred=dest
        while pred != None:
            path.append(pred)
            pred=predecessors.get(pred,None)
        # reverses the array, to display the path nicely
        readable = path[0]

        return(path, new_time)
        
    else : 
            
        neighbor_list = []
        neighbor_times = []
        
        for neighbor in graph[src] :
            #vecinos_v = list(graph[neighbor].keys())
            #print('vecinos_v', vecinos_v)
            #for v in vecinos_v:
            #    if v in visited:
            #        vecinos_v.remove(v)
            #        print('vecinos_v modificado, se le borraron vecinos', vecinos_v)
            if neighbor not in visited:
                neighbor_list.append(neighbor)
                x = graph[src][neighbor][0]['speed_kph']
                if type(x) == list:
                    x = sum(x)
                y = graph[src][neighbor][0]['length']
                if type(y) == list:
                    y = sum(y)
                
                act_time = actualizar_tiempo(x, y, mes, hora, minutos)
                neighbor_times.append(act_time)
                
        print('vecinos', neighbor_list) 
        print('tiempos', neighbor_times) 
        #SE OBTIENE OTRO MÍNIMO, YA QUE EL VECINO MÍNIMO YA FUE VISITADO PERO EL RESTO NO
        siguiente = src
        vv_visitados = True
        while len(neighbor_list) > 0 and vv_visitados: 
            print('Entró al bucle con la neighbor_list', neighbor_list)
            indice_min = neighbor_times.index(min(neighbor_times))
            siguiente = neighbor_list[indice_min]
            print('siguiente sería', siguiente)
            if siguiente in visited:
                print(siguiente, 'ya fue visitado')
                # Se borra de las posibilidades
                neighbor_list.remove(siguiente)
                neighbor_times.remove(neighbor_times[neighbor_times.index(siguiente)])
                print('neighbor_times y neighbor_list sin', siguiente, 'quedan como')
                print(neighbor_times)
                print(neighbor_list)
            else:
                print(siguiente, 'no ha sido visitado, se debería salir del bucle')
                vv_visitados = False
                
            #Revisar la lisa de vecinos nueva: Sí aún tiene vecinos repetir lo anterior, sino se devuelve
        print('Si estaba en un bucle, salió')    
        #SE DEVUELVE SI --> No tiene vecinos    
        if len(neighbor_list) == 0:
            #predecessors buscar el elemento que tiene el value  de siguiente y borrarlo (se agrega al set betados),
            #antes borrarlo guardar su key como siguiente
            #dehacer último paso
            betados.add(siguiente)
            print('Se beto a', siguiente)
            siguiente = [predecessors.pop(key) for key in [siguiente]][0]
            print('ruta, dado que se borró un paso', predecessors)
            old_time = historico[siguiente]['tiempo_arco']
            mes = historico[siguiente]['mes']
            hora = historico[siguiente]['hora']
            minutos= historico[siguiente]['minutos']
            new_time = new_time - old_time
        else:
            print(src, 'Tiene vecinos decentes y siguiente es', siguiente)
            new_time = new_time + min(neighbor_times)
            predecessors[siguiente] = src
            print('ruta', predecessors)
            historico[src] = {'dest':siguiente, 'mes':mes, 'hora': hora, 'minutos':minutos, 'tiempo_arco': min(neighbor_times)}
            visited.add(siguiente)
            print('visitados', visited)
        
        
        return vecino_cercano(graph, siguiente, dest, mes, hora, minutos, new_time, visited, historico, betados, predecessors)

In [16]:
ejemplito = {4:3,3:2,2:1}
# 4 no tiene vecinos
siguiente = 3
print([ejemplito.pop(key) for key in [siguiente]])
ejemplito

[2]


{4: 3, 2: 1}

In [17]:
#grafi = subgrafo(graph, 1882519127, direccion_x, direccion_y, 0, 5)
#a = vecino_cercano(graph, 1882519127, 1552735798, 7, 6, 30, 0, set(), {}, set(), {})
#a

vecinos [5780599855, 1882519126, 1882519124]
tiempos [0.0016582688391038698, 0.00642785, 0.00025969450101832994]
Entró al bucle con la neighbor_list [5780599855, 1882519126, 1882519124]
siguiente sería 1882519124
1882519124 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
1882519127 Tiene vecinos decentes y siguiente es 1882519124
ruta {1882519124: 1882519127}
visitados {1882519124, 1882519127}
vecinos [6050270608]
tiempos [0.0009361507128309573]
Entró al bucle con la neighbor_list [6050270608]
siguiente sería 6050270608
6050270608 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
1882519124 Tiene vecinos decentes y siguiente es 6050270608
ruta {1882519124: 1882519127, 6050270608: 1882519124}
visitados {6050270608, 1882519124, 1882519127}
vecinos [6050270607]
tiempos [0.0010108553971486763]
Entró al bucle con la neighbor_list [6050270607]
siguiente sería 6050270607
6050270607 no ha sido visitado, se debería salir del bucle
Si estab

ruta, dado que se borró un paso {1882519124: 1882519127, 6050270608: 1882519124, 6050270607: 6050270608, 6055795762: 6050270607, 277063741: 6055795762, 6055795755: 277063741, 3997800578: 6055795755, 277063742: 3997800578, 277063743: 277063742, 5131231491: 277063743, 277063744: 5131231491, 4431755693: 277063744, 458570684: 4431755693, 277063745: 458570684, 277063746: 277063745, 1956066936: 277063746, 277063747: 1956066936, 1956066928: 277063747, 6055795763: 1956066928, 277063748: 6055795763, 458570583: 277063748, 5780600007: 458570583, 5780599896: 5780600007, 5780600073: 5780599896, 458570586: 5780600073, 5780600071: 458570586, 5780599954: 5780600071, 458570655: 5780599954, 6932357774: 458570655, 6932357775: 6932357774, 458570568: 6932357775, 5780599953: 458570568, 5780600072: 5780599953, 458570569: 5780600072, 5780600048: 458570569, 5780599911: 5780600048, 5780599909: 5780599911, 458570572: 5780599909, 458570542: 458570572, 5780600037: 458570542, 3454354451: 5780600037, 3454354450: 345

siguiente sería 6055795780
6055795780 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
458571238 Tiene vecinos decentes y siguiente es 6055795780
ruta {1882519124: 1882519127, 6050270608: 1882519124, 6050270607: 6050270608, 6055795762: 6050270607, 277063741: 6055795762, 6055795755: 277063741, 3997800578: 6055795755, 277063742: 3997800578, 277063743: 277063742, 5131231491: 277063743, 277063744: 5131231491, 4431755693: 277063744, 458570684: 4431755693, 277063745: 458570684, 277063746: 277063745, 1956066936: 277063746, 277063747: 1956066936, 1956066928: 277063747, 6055795763: 1956066928, 277063748: 6055795763, 458570583: 277063748, 5780600007: 458570583, 5780599896: 5780600007, 5780600073: 5780599896, 458570586: 5780600073, 5780600071: 458570586, 5780599954: 5780600071, 458570655: 5780599954, 6932357774: 458570655, 6932357775: 6932357774, 458570568: 6932357775, 5780599953: 458570568, 5780600072: 5780599953, 458570569: 5780600072, 5780600048: 458570569, 57805999

tiempos []
Si estaba en un bucle, salió
Se beto a 277060965
ruta, dado que se borró un paso {1882519124: 1882519127, 6050270608: 1882519124, 6050270607: 6050270608, 6055795762: 6050270607, 277063741: 6055795762, 6055795755: 277063741, 3997800578: 6055795755, 277063742: 3997800578, 277063743: 277063742, 5131231491: 277063743, 277063744: 5131231491, 4431755693: 277063744, 458570684: 4431755693, 277063745: 458570684, 277063746: 277063745, 1956066936: 277063746, 277063747: 1956066936, 1956066928: 277063747, 6055795763: 1956066928, 277063748: 6055795763, 458570583: 277063748, 5780600007: 458570583, 5780599896: 5780600007, 5780600073: 5780599896, 458570586: 5780600073, 5780600071: 458570586, 5780599954: 5780600071, 458570655: 5780599954, 6932357774: 458570655, 6932357775: 6932357774, 458570568: 6932357775, 5780599953: 458570568, 5780600072: 5780599953, 458570569: 5780600072, 5780600048: 458570569, 5780599911: 5780600048, 5780599909: 5780599911, 458570572: 5780599909, 458570542: 458570572, 57

ruta {1882519124: 1882519127, 6050270608: 1882519124, 6050270607: 6050270608, 6055795762: 6050270607, 277063741: 6055795762, 6055795755: 277063741, 3997800578: 6055795755, 277063742: 3997800578, 277063743: 277063742, 5131231491: 277063743, 277063744: 5131231491, 4431755693: 277063744, 458570684: 4431755693, 277063745: 458570684, 277063746: 277063745, 1956066936: 277063746, 277063747: 1956066936, 1956066928: 277063747, 6055795763: 1956066928, 277063748: 6055795763, 458570583: 277063748, 5780600007: 458570583, 5780599896: 5780600007, 5780600073: 5780599896, 458570586: 5780600073, 5780600071: 458570586, 5780599954: 5780600071, 458570655: 5780599954, 6932357774: 458570655, 6932357775: 6932357774, 458570568: 6932357775, 5780599953: 458570568, 5780600072: 5780599953, 458570569: 5780600072, 5780600048: 458570569, 5780599911: 5780600048, 5780599909: 5780599911, 458570572: 5780599909, 458570542: 458570572, 5780600037: 458570542, 3454354451: 5780600037, 3454354450: 3454354451, 5780599912: 345435

...

4777265119 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
1937482301 Tiene vecinos decentes y siguiente es 4777265119
ruta {1882519124: 1882519127, 6050270608: 1882519124, 6050270607: 6050270608, 6055795762: 6050270607, 277063741: 6055795762, 6055795755: 277063741, 3997800578: 6055795755, 277063742: 3997800578, 277063743: 277063742, 5131231491: 277063743, 277063744: 5131231491, 4431755693: 277063744, 458570684: 4431755693, 277063745: 458570684, 277063746: 277063745, 1956066936: 277063746, 277063747: 1956066936, 1956066928: 277063747, 6055795763: 1956066928, 277063748: 6055795763, 458570583: 277063748, 5780600007: 458570583, 5780599896: 5780600007, 5780600073: 5780599896, 458570586: 5780600073, 5780600071: 458570586, 5780599954: 5780600071, 458570655: 5780599954, 6932357774: 458570655, 6932357775: 6932357774, 458570568: 6932357775, 5780599953: 458570568, 5780600072: 5780599953, 458570569: 5780600072, 5780600048: 458570569, 5780599911: 5780600048, 5780599909

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



vecinos [1445204295]
tiempos [9.778869778869779e-05]
Entró al bucle con la neighbor_list [1445204295]
siguiente sería 1445204295
1445204295 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
7418173951 Tiene vecinos decentes y siguiente es 1445204295
ruta {1882519124: 1882519127, 6050270608: 1882519124, 6050270607: 6050270608, 6055795762: 6050270607, 277063741: 6055795762, 6055795755: 277063741, 3997800578: 6055795755, 277063742: 3997800578, 277063743: 277063742, 5131231491: 277063743, 277063744: 5131231491, 4431755693: 277063744, 458570684: 4431755693, 277063745: 458570684, 277063746: 277063745, 1956066936: 277063746, 277063747: 1956066936, 1956066928: 277063747, 6055795763: 1956066928, 277063748: 6055795763, 458570583: 277063748, 5780600007: 458570583, 5780599896: 5780600007, 5780600073: 5780599896, 458570586: 5780600073, 5780600071: 458570586, 5780599954: 5780600071, 458570655: 5780599954, 6932357774: 458570655, 6932357775: 6932357774, 458570568: 6932357775

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



RecursionError: maximum recursion depth exceeded while calling a Python object

In [ ]:
predecessors = {1882519124: 1882519127, 6050270608: 1882519124, 6050270607: 6050270608, 6055795762: 6050270607, 277063741: 6055795762, 6055795755: 277063741, 3997800578: 6055795755, 277063742: 3997800578, 277063743: 277063742, 5131231491: 277063743, 277063744: 5131231491, 4431755693: 277063744, 458570684: 4431755693, 277063745: 458570684, 277063746: 277063745, 1956066936: 277063746, 277063747: 1956066936, 1956066928: 277063747, 6055795763: 1956066928, 277063748: 6055795763, 458570583: 277063748, 5780600007: 458570583, 5780599896: 5780600007, 5780600073: 5780599896, 458570586: 5780600073, 5780600071: 458570586, 5780599954: 5780600071, 458570655: 5780599954, 6932357774: 458570655, 6932357775: 6932357774, 458570568: 6932357775, 5780599953: 458570568, 5780600072: 5780599953, 458570569: 5780600072, 5780600048: 458570569, 5780599911: 5780600048, 5780599909: 5780599911, 458570572: 5780599909, 458570542: 458570572, 5780600037: 458570542, 3454354451: 5780600037, 3454354450: 3454354451, 5780599912: 3454354450, 5780600036: 5780599912, 458570546: 5780600036, 5780599907: 458570546, 4431741708: 5780599907, 3035244389: 4431741708, 4379802867: 3035244389, 1790882954: 4379802867, 4431741709: 1790882954, 4788544995: 4431741709, 6932422700: 4788544995, 6932422697: 6932422700, 6932422696: 6932422697, 6932422695: 6932422696, 6932422699: 6932422695, 6932422694: 6932422699, 6932422693: 6932422694, 6932422698: 6932422693, 4431741712: 6932422698, 4379802858: 4431741712, 4379802860: 4379802858, 6055795692: 4379802860, 6055795687: 6055795692, 4379802866: 6055795687, 6055795697: 4379802866, 4431741705: 6055795697, 6932422692: 4431741705, 6932422691: 6932422692, 4431741707: 6932422691}
path=[]
pred = 6932422691
while pred != None:
    path.append(pred)
    pred=predecessors.get(pred,None)
# reverses the array, to display the path nicely
readable = path[0]
print(path[::-1])

In [ ]:
path = [1882519127, 1882519124, 6050270608, 6050270607, 6055795762, 277063741, 6055795755, 3997800578, 277063742, 277063743, 5131231491, 277063744, 4431755693, 458570684, 277063745, 277063746, 1956066936, 277063747, 1956066928, 6055795763, 277063748, 458570583, 5780600007, 5780599896, 5780600073, 458570586, 5780600071, 5780599954, 458570655, 6932357774, 6932357775, 458570568, 5780599953, 5780600072, 458570569, 5780600048, 5780599911, 5780599909, 458570572, 458570542, 5780600037, 3454354451, 3454354450, 5780599912, 5780600036, 458570546, 5780599907, 4431741708, 3035244389, 4379802867, 1790882954, 4431741709, 4788544995, 6932422700, 6932422697, 6932422696, 6932422695, 6932422699, 6932422694, 6932422693, 6932422698, 4431741712, 4379802858, 4379802860, 6055795692, 6055795687, 4379802866, 6055795697, 4431741705, 6932422692, 6932422691]
fig, ax = ox.plot_graph_route(grafi, path)

In [ ]:
grafi[6932422690]

In [ ]:
graph[6932422691]

In [ ]:
def subgrafoX(graph, src, dest, k):
    k_rutas = ox.distance.k_shortest_paths(graph, src, dest, k, weight='Tiempos de Viaje')
    lista_sets = []
    for counter, path in enumerate(k_rutas):
        lista_sets.append(set(path))
        if counter == k-1:
             break
    nodos = list(reduce(operator.or_, lista_sets))
    subgrafo = graph.subgraph(nodos)
    return subgrafo

**Actualizamos valores de arcos en el grafo de santiago, ahora se llamará G contiene velocidad con congestión**

In [ ]:
# G  = ox.utils_graph.graph_from_gdfs(nodes , edges , graph_attrs = None)

In [ ]:
# nodesG, edgesG = ox.graph_to_gdfs(G)

**Ahora podemos calcular la ruta mínima entre dos nodos, bajo cualquier atributo de arco**

In [ ]:
nodos = pd.read_csv("coord_cercanos.csv")

In [ ]:
list_id = []
for row in nodos.iterrows():
    list_id.append(row[1][3])
    
list_id


In [ ]:
ClientesAprox = pd.read_csv("coord_cercanos.csv")
direccion_x =[]
direccion_y =[]
for row in ClientesAprox.iterrows():
    direccion_x.append(row[1][1])
    direccion_y.append(row[1][2])

**Función que debe ir calculando los costos que difieren del tiempo**

(1286.7*(edges[lenght]/1000)) ---------------> Todos los arcos

(sumar + 21378) -----------------------------> Arcos salientes del depot

In [ ]:
def costos_agregados(path):
    agregados = 0
    for n in range(len(path)-1):
        if path[len(path)-1] == 267454352 and agregados == 0:
            agregados += 21378
        else:
            agregados += (1286.7 * graph[path[n+1]][path[n]][0]['length'])/1000
    return (agregados)

In [ ]:
# Calculate the shortest path dinamic time
def rutas_min_pares(G, list_id, mes, hora, minutos):
    tiempo_inicial = time() 
    dic_rutas = {}
    #G = ox.utils_graph.graph_from_gdfs(nodes , edges , graph_attrs = None)
    visitados = set()
    subgrafos = {}
    for n1 in list_id:
        for n2 in list_id:
            if n1 != n2 and nx.has_path(G, n1,n2):
                if (n1, n2) not in visitados:
                    subg = subgrafo(G, n1, direccion_x, direccion_y, list_id.index(n1), list_id.index(n2))
                    subgrafos[(n2, n1)] = subg
                    visitados.add((n2, n1))
                else:
                    subg = subgrafos[(n2, n1)]
                path, tiempo = dijkstra_tiempo(subg, n1, n2, mes, hora, minutos,set(), {}, {})
                print('-------------------------------------------------------------------------------------------------------------------------------------------------')
                print('Encontro ruta min con Dijsktra del par de nodos', (n1, n2))
                print('-------------------------------------------------------------------------------------------------------------------------------------------------')
                costo_agregado = costos_agregados(path)
                dic_rutas[(path[0], path[-1])] = [tiempo, costo_agregado]           
    tiempo_final = time() 
    tiempo_ejecucion = tiempo_final - tiempo_inicial
    print ('El tiempo de ejecucion en minutos fue:', tiempo_ejecucion/60)
    return(dic_rutas)

In [ ]:
dic_rutas = (rutas_min_pares(G, list_id, 6, 9, 0))

In [ ]:
print(dic_rutas)

Notamos que al ocupar el método 'haversine' se repite un nodo, debido a la cercania. De modo que dejaremos ese nodo con su id euclidiano.

**Revisamos todos los pares de nodos que efectivamente no tienen ruta entre sí**

In [ ]:
pares_sin_ruta = []
for n1 in list_id:
        for n2 in list_id:
            if n1 != n2 and nx.has_path(G, n1, n2)==False:
                pares_sin_ruta.append((n1, n2))
                
print('Los siguientes pares no tienen rutas entre sí:', pares_sin_ruta)

Hay 11 pares sin ruta entre sí

In [ ]:
len(pares_sin_ruta)

In [ ]:
diccionario_nodos = {}
list_id = []
i = 0
for row in nodos.iterrows():
    list_id.append(row[1][3])
    diccionario_nodos[row[1][3]] = i
    i+=1
print(diccionario_nodos)

No están existiendo conexiones salientes de los nodos 0, 2 y 3.

In [ ]:
pares = []
for par in pares_sin_ruta:
    pares.append((diccionario_nodos[par[0]],diccionario_nodos[par[1]]))
print(pares)    

In [ ]:
list_id = [1882519127, 265690338, 4441341769]
tamaños = []
subgrafos = {}
for i in list_id:
    for j in list_id: 
        if i != j:
            grafito = subgrafo(graph, i, direccion_x, direccion_y, list_id.index(i), list_id.index(j))
            tamaños.append(len(grafito.nodes))
            subgrafos[(i, j)] = grafito
            if j not in grafito:
                print(diccionario_nodos[j],' no está en el subgrafo generado desde', diccionario_nodos[i])

In [ ]:
print(subgrafos)

In [ ]:
print(max(tamaños))

In [ ]:
print(direccion_y)

In [ ]:
prueba = ox.distance.great_circle_vec(direccion_x[5], direccion_y[5], direccion_x[8], direccion_y[8], earth_radius = 6371009)
print(prueba/100)

In [ ]:
len(grafito.nodes)

In [ ]:
247688-219954


# -----------------------------------------------------------------------------------------------------

In [ ]:
"""# Necesitamos ahora, crear la estructura de grafo sin calles con los costos reales en los arcos entre cada par o-d
#Se importa la libreria networkx como nx

import networkx as nx

#Se importa la libreria pyplot de matplotlib como plt

import matplotlib.pyplot as plt

#Se crea un grafo asimétrico vacio

G = nx.DiGraph()

#Se crean los nodos:

#Se crean los nodos depot + clientes

G.add_nodes_from(list_id)

#Se crean los arcos entre los nodos
for a in dic_rutas:
    G.add_edge(a[0], a[1])
    G.edges[(a[0], a[1])]['Costo']= dic_rutas[a]
for n in G.nodes:
    if n == 267454352:
        G.nodes[n]['Depot'] = True
    else:
        G.nodes[n]['Depot'] = False
    
#Se dibuja el grafo

nx.draw(G, node_size = 12, font_size=1)

#Se muestra en pantalla

plt.show()"""



In [ ]:
"""G.nodes"""

In [ ]:
"""G.edges"""

In [ ]:
"""G.edges[(3485642555, 4765300244)]"""

In [ ]:
"""G.nodes[613890784]"""

# Creación de datos

In [ ]:
"""n = list_id.copy()# Clientes
camiones = [k for k in range (1,4)]
list_id.remove(267454352)
clientes = list_id
u={1: 5500, 2:5500, 3:5500}

import numpy as np
rnd=np.random
rnd.seed(0)

q={i:rnd.randint(500, 1000) for i in clientes}"""

In [ ]:
"""print(n)
print(clientes)
print(camiones)
print(u)
print(q)
print(list_id)"""

In [ ]:
"""import matplotlib.pyplot as plt

plt.figure(figsize=(12,5))
plt.scatter(direccion_x,direccion_y,color="green")

for i in clientes:
       plt.annotate('$q_{%d}=%d$'%(i,q[i]),(direccion_x[clientes.index(i)],direccion_y[clientes.index(i)]))
    
plt.plot(direccion_x[0],direccion_y[0],color='red',marker='s')
plt.annotate('DC',(direccion_x[0],direccion_y[0]))

plt.xlabel("Eje X")
plt.ylabel("Eje Y")
plt.title("Gráfico de Nodos | VRP")

plt.show()"""



In [ ]:
"dic_rutas[(3485642555, 4765300244)]"

In [ ]:
""""arcos={i for i in dic_rutas.keys()}
# esto es literal dic_rutas
#distancia={(i,j):np.hypot(direccion_x[i]-direccion_x[j],direccion_y[i]-direccion_y[j]) 
          # for i in nodos for j in nodos if i!=j}
arcos"""

In [ ]:
"""plt.figure(figsize=(12,5))
plt.scatter(direccion_x,direccion_y,color="green")

for i in clientes:
    plt.annotate('$q_{%d}$'%(i),(direccion_x[clientes.index(i)],direccion_y[clientes.index(i)]))
    
plt.plot(direccion_x[0],direccion_y[0],color='red',marker='s')
plt.annotate('DC',(direccion_x[0],direccion_y[0]))

for i, j in arcos:
    plt.plot([direccion_x[n.index(i)],direccion_x[n.index(j)]],[direccion_y[n.index(i)],direccion_y[n.index(j)]],color="blue",alpha=0.3)
    #plt.annotate('C=%d'%dic_rutas[(i,j)], ((direccion_x[n.index(i)]+direccion_x[n.index(j)])/2, (direccion_y[n.index(i)]+direccion_y[n.index(j)])/2))
plt.xlabel("Eje X")
plt.ylabel("Eje Y")
plt.title("Grafo completo, arcos entre todo par de nodos donde existe ruta| VRP")


plt.show()"""

Fuente: https://nbviewer.jupyter.org/github/CplexPython/Cplex-Python/blob/master/VRP/CVRP%20%7C%20Cplex%20%26%20Python%20.ipynb

# Utilizando Heurísticas para resolver VRP

In [ ]:
"""# Plot the shortest path
fig, ax = ox.plot_graph_route(G, route)"""